Kütüphanelerin Yüklenmesi

In [ ]:
from datasets import load_dataset
import pandas as pd 


ValueError: numpy.dtype size changed, may indicate binary incompatibility. Expected 96 from C header, got 88 from PyObject

In [7]:
#verileri bart ile eğitme burada koleksiyon içerisindeki veriler tanımlanmalı 
# Load model directly
from transformers import AutoModel,AutoTokenizer
from transformers import (WEIGHTS_NAME, BertConfig,
                                  BertForQuestionAnswering, BertTokenizer)
from torch.utils.data import DataLoader, SequentialSampler, TensorDataset

#from utils import (get_answer, input_to_squad_example,squad_examples_to_features, to_list)
import collections
# Load model directly
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

OSError: [WinError 126] Belirtilen modül bulunamadı. Error loading "c:\gitProjects\deneme\.venv\Lib\site-packages\torch\lib\fbgemm.dll" or one of its dependencies.

Train ve Test Verilerine İlişkin Databaselerin İçerisindeki Bilgilerin Alınması 

In [8]:
#birleştirilcek dosyaların listesi 
train_files=['C:\\gitProjects\\oak\\data\\train-00000-of-00007.parquet','C:\\gitProjects\\oak\\data\\train-00001-of-00007.parquet','C:\\gitProjects\\oak\\data\\train-00002-of-00007.parquet','C:\\gitProjects\\oak\\data\\train-00003-of-00007.parquet','C:\\gitProjects\\oak\\data\\train-00004-of-00007.parquet']
test_files=['C:\\gitProjects\\oak\\data\\train-00005-of-00007.parquet','C:\\gitProjects\\oak\\data\\train-00006-of-00007.parquet']

In [ ]:
#dosyaları yükleyin ve birleştirin
train_dfs=[pd.read_parquet(file) for file in train_files]
test_dfs=[pd.read_parquet(file) for file in test_files]

In [ ]:
#parque dosyalarının birleştirilmesi
train_df=pd.concat(train_dfs,ignore_index=True)
test_df=pd.concat(test_dfs,ignore_index=True)

print(train_df.head())
print(train_df.head())

In [2]:
#train  ve test dosyaları oluşturma 
train_df.to_parquet('C:\\gitProjects\\deneme\\egitim\\train_Egitim\\merged_train.parquet')
test_df.to_parquet('C:\\gitProjects\\deneme\\test_Egitim\\merged_train.parquet')

NameError: name 'train_df' is not defined

In [3]:
#test ve train yollarını belirleme ve test, traindeki önemli sütunları alma
train_file_path=('C:\\gitProjects\\deneme\\egitim\\train_Egitim\\merged_train.parquet')
test_file_path=('C:\\gitProjects\\deneme\\egitim\\test_Egitim\\merged_train.parquet')

train_df=pd.read_parquet(train_file_path,columns=['Prompt_ID','Prompt','Response','Category','Subcategory','Prompt_token_length'])
test_df=pd.read_parquet(test_file_path,columns=['Prompt_ID','Prompt','Response','Category','Subcategory','Prompt_token_length'])

print(train_df.head())
print(test_df.head())

                          Prompt_ID  \
0  bb26c95639b18fd88857bf0964cd1fb5   
1  56743c1870327184e058292a34ce12a8   
2  88aa2f72d37cb8671ff68a6f481e382b   
3  703c086f7ffd9d8cc0497e82732860c7   
4  a310cb6ed3f48e721473ec0525239e4e   

                                              Prompt  \
0  What were the crucial factors that contributed...   
1  Create a comprehensive guide to understanding ...   
2  Explore the historical significance and impact...   
3  How can advanced data analytics be leveraged t...   
4  Design a comprehensive diversity training prog...   

                                            Response  \
0  **Crucial Factors Contributing to the Success ...   
1  ## Comprehensive Guide to Weather Front Types:...   
2  ## The Fall of the Berlin Wall: Historical Sig...   
3  **1. Real-Time Sentiment Analysis:**\n\n* Anal...   
4  **Phase 1: Awareness and Self-Reflection**\n\n...   

                      Category                  Subcategory  \
0              Voskhod progr

Modelin Tokenizer ve İsminin Girilmesi

In [3]:
from transformers import T5Tokenizer, T5ForConditionalGeneration

tokenizer = T5Tokenizer.from_pretrained("google/flan-t5-xxl")
model = T5ForConditionalGeneration.from_pretrained("google/flan-t5-xxl")

OSError: [WinError 126] Belirtilen modül bulunamadı. Error loading "c:\gitProjects\deneme\.venv\Lib\site-packages\torch\lib\fbgemm.dll" or one of its dependencies.

MongoDb üzerinden önemli sütunların çekilmesi

In [17]:
from pymongo import MongoClient
import pandas as pd

# MongoDB connection settings

def get_mongodb(database_name='yeniDatabase', collection_name='train', host='localhost', port=27017):
    """
    MongoDB connection and collection selection
    """
    client = MongoClient(f'mongodb://{host}:{port}/')
    db = client[database_name]
    collection = db[collection_name]
    return collection

# Function to load dataset into MongoDB
def dataset_read():
    train_file_path = ('C:\\gitProjects\\deneme\\egitim\\train_Egitim\\merged_train.parquet')
    data = pd.read_parquet(train_file_path, columns=['Prompt_ID', 'Prompt', 'Response', 'Category', 'Subcategory', 'Prompt_token_length'])
    data_dict = data.to_dict("records")

    # Get the MongoDB collection
    source_collection = get_mongodb(database_name='yeniDatabase', collection_name='train')  # Collection for translation

    # Insert data into MongoDB
    source_collection.insert_many(data_dict)

    print("Data successfully loaded into MongoDB.")
    return source_collection

# Call the function to load the dataset into MongoDB
source_collection = dataset_read()

Data successfully loaded into MongoDB.


In [18]:
from pymongo import MongoClient
import pandas as pd

# MongoDB connection settings

def get_mongodb(database_name='yeniDatabase', collection_name='test', host='localhost', port=27017):
    """
    MongoDB connection and collection selection
    """
    client = MongoClient(f'mongodb://{host}:{port}/')
    db = client[database_name]
    collection = db[collection_name]
    return collection

# Function to load dataset into MongoDB
def dataset_read():
    train_file_path = ('C:\\gitProjects\\deneme\\egitim\\test_Egitim\\merged_train.parquet')
    data = pd.read_parquet(train_file_path, columns=['Prompt_ID', 'Prompt', 'Response', 'Category', 'Subcategory', 'Prompt_token_length'])
    data_dict = data.to_dict("records")

    # Get the MongoDB collection
    source_collection = get_mongodb(database_name='yeniDatabase', collection_name='test')  # Collection for translation

    # Insert data into MongoDB
    source_collection.insert_many(data_dict)

    print("Data successfully loaded into MongoDB.")
    return source_collection

# Call the function to load the dataset into MongoDB
source_collection = dataset_read()

Data successfully loaded into MongoDB.


In [1]:
# uygulama için kullanılcak olan özelliklerin tanımlanması
from transformers import BertTokenizer,BertForQuestionAnswering,BertConfig
class QA:
    def __init__(self,model_path: str):
        self.max_seq_length = 384 #max seq
        self.doc_stride = 128 #stride 
        self.do_lower_case = False
        self.max_query_length = 30
        self.n_best_size = 3
        self.max_answer_length = 30
        self.version_2_with_negative = False
        #modelin yüklenmesi
        self.model, self.tokenizer = self.load_model(model_path)
        #hangi işlmecinin kullanıldığının belirlenmesi
        if torch.cuda.is_available():
            self.device = 'cuda'
        else:
            self.device = 'cpu'
        self.model.to(self.device)
        self.model.eval()
        
        # This function is used to load the model
    def load_model(self,model_path: str,do_lower_case=False):
        config = BertConfig.from_pretrained(model_path + "C:\\gitProjects\\deneme\\egitim\\train_Egitim")
        tokenizer = BertTokenizer.from_pretrained(model_path, do_lower_case=do_lower_case)
        model = BertForQuestionAnswering.from_pretrained(model_path, from_tf=False, config=config)
        return model, tokenizer


c:\gitProjects\deneme\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


OSError: [WinError 126] Belirtilen modül bulunamadı. Error loading "c:\gitProjects\deneme\.venv\Lib\site-packages\torch\lib\fbgemm.dll" or one of its dependencies.